In [25]:
from transformers import BasicTokenizer, EarlyStoppingCallback, Trainer
from datasets import concatenate_datasets, load_from_disk
import kagglehub
import optuna
import torch
import math
import base

In [26]:
base.reset_seed()

In [27]:
if torch.cuda.is_available():
    device = torch.device("cuda")
    print("GPU is available and will be used:", torch.cuda.get_device_name(0))
else:
    device = torch.device("cpu")
    print("GPU is not available, using CPU.")

GPU is available and will be used: NVIDIA A100 80GB PCIe MIG 2g.20gb


In [28]:
my_glove = kagglehub.dataset_download("thanakomsn/glove6b300dtxt")
print(my_glove)

/home/jovyan/.cache/kagglehub/datasets/thanakomsn/glove6b300dtxt/versions/1


In [29]:
GLOVE_FILE = f"{my_glove}/glove.6B.300d.txt"
DATASET = "trec"

In [30]:
train_data = load_from_disk(f"~/data/{DATASET}/train-logits_fine")
eval_data = load_from_disk(f"~/data/{DATASET}/eval-logits_fine")
test_data = load_from_disk(f"~/data/{DATASET}/test-logits_fine")

all_train_data = load_from_disk(f"~/data/{DATASET}/train-logits-augmented_fine")

all_data = concatenate_datasets([load_from_disk(file) for file in [f"~/data/{DATASET}/eval-logits_fine", f"~/data/{DATASET}/test-logits_fine", f"~/data/{DATASET}/train-logits-augmented_fine"]])
tokenizer = BasicTokenizer(do_lower_case=True)

In [31]:
train_data_tokens = list(map(lambda e: tokenizer.tokenize(e["sentence"]), train_data))
eval_data_tokens = list(map(lambda e: tokenizer.tokenize(e["sentence"]), eval_data))
test_data_tokens = list(map(lambda e: tokenizer.tokenize(e["sentence"]), test_data))

all_train_data_tokens = list(map(lambda e: tokenizer.tokenize(e["sentence"]), all_train_data))

all_data_tokens = list(map(lambda e: tokenizer.tokenize(e["sentence"]), all_data))

In [32]:
vocab = base.get_vocab(all_data_tokens)

In [33]:
word_index = dict(zip(vocab, range(len(vocab))))

In [34]:
embeddings_index = base.get_embeddings_indeces(GLOVE_FILE)

Found 400000 word vectors.


In [35]:
print(len(vocab))
num_tokens = len(vocab) + 2
embedding_dim = 300

8766


In [36]:
embedding_matrix = base.get_embedding_matrix(num_tokens, embedding_dim, word_index, embeddings_index)

Converted 8551 words (215) misses


In [37]:
train_data_index = list(map(lambda x: list(map(lambda y: word_index[y], x)),train_data_tokens))
eval_data_index = list(map(lambda x: list(map(lambda y: word_index[y], x)),eval_data_tokens))
test_data_index = list(map(lambda x: list(map(lambda y: word_index[y], x)),test_data_tokens))

all_train_data_index = list(map(lambda x: list(map(lambda y: word_index[y], x)),all_train_data_tokens))

In [38]:
train_padded_data = list(map(lambda x: base.padd(x,60), train_data_index))
eval_padded_data = list(map(lambda x: base.padd(x,60), eval_data_index))
test_padded_data = list(map(lambda x: base.padd(x,60), test_data_index))

all_train_padded_data = list(map(lambda x: base.padd(x,60), all_train_data_index))

In [39]:
train_data = train_data.add_column("input_ids", train_padded_data)
eval_data = eval_data.add_column("input_ids", eval_padded_data)
test_data = test_data.add_column("input_ids", test_padded_data)

all_train_data = all_train_data.add_column("input_ids", all_train_padded_data)

In [40]:
num_epochs = 30
batch_size = 128

In [41]:
#Nápočet epoch na steps
data_length = len(train_data)
min_r = math.ceil(data_length/batch_size)*5
max_r = math.ceil(data_length/batch_size)*num_epochs
warm_up = math.ceil(data_length/batch_size/10)

In [42]:
def hp_space(trial):
    params =  {
        "learning_rate": trial.suggest_float("learning_rate", 1e-5, 5e-3, log=True),
        "weight_decay": trial.suggest_float("weight_decay", 0, 1e-2, step=1e-3),
        "adam_beta1" : trial.suggest_float("adam_beta1", 0.9, 0.99, step=0.01),
        "warmup_steps" : trial.suggest_int("warmup_steps", 0, warm_up)
    }   
    print(f"Trial {trial.number} with params: {params}")
    return params

In [43]:
pruner = optuna.pruners.HyperbandPruner(min_resource=min_r, max_resource=max_r, reduction_factor=2, bootstrap_count=2)
sampler = optuna.samplers.TPESampler(seed=42, multivariate=True)

/usr/local/lib/python3.10/dist-packages/optuna/_experimental.py:31: ExperimentalWarning: Argument ``multivariate`` is an experimental feature. The interface can change in the future.
  warnings.warn(


In [44]:
def get_BiLSTM():
    return base.BiLSTMClassifier(embedding_matrix=embedding_matrix, embedding_dim=embedding_dim, fc_dim=400, hidden_dim=300, output_dim=50)

In [45]:
base.reset_seed()

In [46]:
training_args = base.get_training_args(output_dir=f"~/results/{DATASET}/bilstm-base_fine_hp-search", logging_dir=f"~/logs/{DATASET}/bilstm-base_fine_hp-search", epochs=num_epochs, batch_size=batch_size)

In [47]:
trainer = Trainer(
    args=training_args,
    train_dataset=train_data,
    eval_dataset=eval_data,
    compute_metrics=base.compute_metrics,
    model_init = lambda: get_BiLSTM(),
    #callbacks = [EarlyStoppingCallback(early_stopping_patience = 4)]
)
  

In [48]:
best_trial = trainer.hyperparameter_search(
    direction="maximize",
    backend="optuna",
    hp_space=hp_space,
    compute_objective=lambda metrics: metrics["eval_f1"],
    pruner=pruner,
    sampler=sampler,
    study_name="Test-base",
    n_trials=150
)

[I 2025-03-15 09:38:56,470] A new study created in memory with name: Test-base


Trial 0 with params: {'learning_rate': 0.0001025350969016849, 'weight_decay': 0.01, 'adam_beta1': 0.97, 'warmup_steps': 2}


[I 2025-03-15 09:39:42,963] Trial 0 pruned. 


Trial 1 with params: {'learning_rate': 2.6368755339723032e-05, 'weight_decay': 0.001, 'adam_beta1': 0.9, 'warmup_steps': 4}


[I 2025-03-15 09:40:05,590] Trial 1 pruned. 


...

[I 2025-03-15 13:44:53,864] Trial 147 pruned. 


Trial 148 with params: {'learning_rate': 0.002935639351709915, 'weight_decay': 0.004, 'adam_beta1': 0.9, 'warmup_steps': 0}


[I 2025-03-15 13:46:35,009] Trial 148 pruned. 


Trial 149 with params: {'learning_rate': 0.004424007612483057, 'weight_decay': 0.004, 'adam_beta1': 0.9, 'warmup_steps': 0}


[I 2025-03-15 13:48:59,825] Trial 149 finished with value: 0.6925547327118019 and parameters: {'learning_rate': 0.004424007612483057, 'weight_decay': 0.004, 'adam_beta1': 0.9, 'warmup_steps': 0}. Best is trial 45 with value: 0.7063463805279003.


In [49]:
print(best_trial)

BestRun(run_id='45', objective=0.7063463805279003, hyperparameters={'learning_rate': 0.004693546493886514, 'weight_decay': 0.002, 'adam_beta1': 0.9, 'warmup_steps': 1}, run_summary=None)


In [50]:
base.reset_seed()

In [51]:
training_args = base.get_training_args(output_dir=f"~/results/{DATASET}/bilstm-distill_fine_hp-search", logging_dir=f"~/logs/{DATASET}/bilstm-distill_fine_hp-search", remove_unused_columns=False, epochs=num_epochs, batch_size=batch_size)

In [52]:
def hp_space(trial):
    params =  {
        "learning_rate": trial.suggest_float("learning_rate", 1e-5, 5e-3, log=True),
        "weight_decay": trial.suggest_float("weight_decay", 0, 1e-2, step=1e-3),
        "adam_beta1" : trial.suggest_float("adam_beta1", 0.9, 0.99, step=0.01),
        "warmup_steps" : trial.suggest_int("warmup_steps", 0, warm_up),
        "lambda_param": trial.suggest_float("lambda_param",0,1,step=.1),
        "temperature": trial.suggest_float("temperature", 2,7, step=.5)
    }
    print(f"Trial {trial.number} with params: {params}")
    return params

In [53]:
pruner = optuna.pruners.HyperbandPruner(min_resource=min_r, max_resource=max_r, reduction_factor=2, bootstrap_count=2)
sampler = optuna.samplers.TPESampler(seed=42, multivariate=True)

/usr/local/lib/python3.10/dist-packages/optuna/_experimental.py:31: ExperimentalWarning: Argument ``multivariate`` is an experimental feature. The interface can change in the future.
  warnings.warn(


In [54]:
trainer = base.DistilTrainer(
    args=training_args,
    train_dataset=eval_data,
    eval_dataset=test_data,
    compute_metrics=base.compute_metrics,
    model_init = lambda: get_BiLSTM(),
    #callbacks = [EarlyStoppingCallback(early_stopping_patience = 4)]
)
  

In [55]:
best_trial2 = trainer.hyperparameter_search(
    direction="maximize",
    backend="optuna",
    hp_space=hp_space,
    compute_objective=lambda metrics: metrics["eval_f1"],
    pruner=pruner,
    sampler=sampler,
    study_name="Test-destilace",
    n_trials=150
)

[I 2025-03-15 13:49:00,152] A new study created in memory with name: Test-destilace


Trial 0 with params: {'learning_rate': 0.0001025350969016849, 'weight_decay': 0.01, 'adam_beta1': 0.97, 'warmup_steps': 2, 'lambda_param': 0.1, 'temperature': 2.5}


[I 2025-03-15 13:50:29,574] Trial 0 pruned. 


Trial 1 with params: {'learning_rate': 1.4347159517201392e-05, 'weight_decay': 0.009000000000000001, 'adam_beta1': 0.96, 'warmup_steps': 3, 'lambda_param': 0.0, 'temperature': 7.0}


[I 2025-03-15 13:52:48,363] Trial 1 finished with value: 0.004719004719004719 and parameters: {'learning_rate': 1.4347159517201392e-05, 'weight_decay': 0.009000000000000001, 'adam_beta1': 0.96, 'warmup_steps': 3, 'lambda_param': 0.0, 'temperature': 7.0}. Best is trial 1 with value: 0.004719004719004719.


...

[I 2025-03-15 19:18:48,995] Trial 147 finished with value: 0.2683578976462126 and parameters: {'learning_rate': 0.0013506151458172716, 'weight_decay': 0.0, 'adam_beta1': 0.9500000000000001, 'warmup_steps': 0, 'lambda_param': 0.2, 'temperature': 3.0}. Best is trial 105 with value: 0.48810144914827314.


Trial 148 with params: {'learning_rate': 0.0037447250623325926, 'weight_decay': 0.001, 'adam_beta1': 0.9500000000000001, 'warmup_steps': 0, 'lambda_param': 0.30000000000000004, 'temperature': 2.0}


[I 2025-03-15 19:21:17,358] Trial 148 finished with value: 0.4029932102759337 and parameters: {'learning_rate': 0.0037447250623325926, 'weight_decay': 0.001, 'adam_beta1': 0.9500000000000001, 'warmup_steps': 0, 'lambda_param': 0.30000000000000004, 'temperature': 2.0}. Best is trial 105 with value: 0.48810144914827314.


Trial 149 with params: {'learning_rate': 0.0012829186602505733, 'weight_decay': 0.005, 'adam_beta1': 0.93, 'warmup_steps': 1, 'lambda_param': 0.0, 'temperature': 7.0}


[I 2025-03-15 19:23:39,330] Trial 149 finished with value: 0.28782323812439825 and parameters: {'learning_rate': 0.0012829186602505733, 'weight_decay': 0.005, 'adam_beta1': 0.93, 'warmup_steps': 1, 'lambda_param': 0.0, 'temperature': 7.0}. Best is trial 105 with value: 0.48810144914827314.


In [56]:
print(best_trial2)

BestRun(run_id='105', objective=0.48810144914827314, hyperparameters={'learning_rate': 0.004107822923895355, 'weight_decay': 0.003, 'adam_beta1': 0.93, 'warmup_steps': 0, 'lambda_param': 0.2, 'temperature': 2.5}, run_summary=None)


In [57]:
base.reset_seed()

In [58]:
training_args = base.get_training_args(output_dir=f"~/results/{DATASET}/bilstm-base_fine_aug_hp-search", logging_dir=f"~/logs/{DATASET}/bilstm-base_fine_aug_hp-search", epochs=num_epochs, batch_size=batch_size)

In [59]:
#Nápočet epoch na steps
data_length = len(all_train_data)
min_r = math.ceil(data_length/batch_size)*5
max_r = math.ceil(data_length/batch_size)*num_epochs
warm_up = math.ceil(data_length/batch_size/10)

In [60]:
def hp_space(trial):
    params =  {
        "learning_rate": trial.suggest_float("learning_rate", 1e-5, 5e-3, log=True),
        "weight_decay": trial.suggest_float("weight_decay", 0, 1e-2, step=1e-3),
        "adam_beta1" : trial.suggest_float("adam_beta1", 0.9, 0.99, step=0.01),
        "warmup_steps" : trial.suggest_int("warmup_steps", 0, warm_up),
    }
    print(f"Trial {trial.number} with params: {params}")
    return params

In [61]:
pruner = optuna.pruners.HyperbandPruner(min_resource=min_r, max_resource=max_r, reduction_factor=2, bootstrap_count=2)
sampler = optuna.samplers.TPESampler(seed=42, multivariate=True)

/usr/local/lib/python3.10/dist-packages/optuna/_experimental.py:31: ExperimentalWarning: Argument ``multivariate`` is an experimental feature. The interface can change in the future.
  warnings.warn(


In [62]:
trainer = Trainer(
    args=training_args,
    train_dataset=all_train_data,
    eval_dataset=eval_data,
    compute_metrics=base.compute_metrics,
    model_init = lambda: get_BiLSTM(),
    #callbacks = [EarlyStoppingCallback(early_stopping_patience = 4)]
)
  

In [63]:
best_trial3 = trainer.hyperparameter_search(
    direction="maximize",
    backend="optuna",
    hp_space=hp_space,
    compute_objective=lambda metrics: metrics["eval_f1"],
    pruner=pruner,
    sampler=sampler,
    study_name="Test-base-aug",
    n_trials=150
)

[I 2025-03-15 19:23:39,682] A new study created in memory with name: Test-base-aug


Trial 0 with params: {'learning_rate': 0.0001025350969016849, 'weight_decay': 0.01, 'adam_beta1': 0.97, 'warmup_steps': 32}


[I 2025-03-15 19:25:16,160] Trial 0 pruned. 


Trial 1 with params: {'learning_rate': 2.6368755339723032e-05, 'weight_decay': 0.001, 'adam_beta1': 0.9, 'warmup_steps': 46}


[I 2025-03-15 19:26:53,086] Trial 1 pruned. 


...

[I 2025-03-16 09:18:44,735] Trial 147 pruned. 


Trial 148 with params: {'learning_rate': 0.0007989056410281233, 'weight_decay': 0.0, 'adam_beta1': 0.9, 'warmup_steps': 3}


[I 2025-03-16 09:20:16,470] Trial 148 pruned. 


Trial 149 with params: {'learning_rate': 0.0035402095463311564, 'weight_decay': 0.0, 'adam_beta1': 0.93, 'warmup_steps': 25}


[I 2025-03-16 09:29:44,156] Trial 149 finished with value: 0.7551578131716231 and parameters: {'learning_rate': 0.0035402095463311564, 'weight_decay': 0.0, 'adam_beta1': 0.93, 'warmup_steps': 25}. Best is trial 22 with value: 0.777016449838325.


In [64]:
print(best_trial3)

BestRun(run_id='22', objective=0.777016449838325, hyperparameters={'learning_rate': 0.0026826241523527678, 'weight_decay': 0.009000000000000001, 'adam_beta1': 0.92, 'warmup_steps': 27}, run_summary=None)


In [65]:
base.reset_seed()

In [66]:
training_args = base.get_training_args(output_dir=f"~/results/{DATASET}/bilstm-distill_fine_aug_hp-search", logging_dir=f"~/logs/{DATASET}/bilstm-distill_fine_aug_hp-search", remove_unused_columns=False, epochs=num_epochs, batch_size=batch_size)

In [67]:
def hp_space(trial):
    params =  {
        "learning_rate": trial.suggest_float("learning_rate", 1e-5, 5e-3, log=True),
        "weight_decay": trial.suggest_float("weight_decay", 0, 1e-2, step=1e-3),
        "adam_beta1" : trial.suggest_float("adam_beta1", 0.9, 0.99, step=0.01),
        "warmup_steps" : trial.suggest_int("warmup_steps", 0, warm_up),
        "lambda_param": trial.suggest_float("lambda_param",0,1,step=.1),
        "temperature": trial.suggest_float("temperature", 2,7, step=.5)
    }
    print(f"Trial {trial.number} with params: {params}")
    return params

In [68]:
pruner = optuna.pruners.HyperbandPruner(min_resource=min_r, max_resource=max_r, reduction_factor=2, bootstrap_count=2)
sampler = optuna.samplers.TPESampler(seed=42, multivariate=True)

/usr/local/lib/python3.10/dist-packages/optuna/_experimental.py:31: ExperimentalWarning: Argument ``multivariate`` is an experimental feature. The interface can change in the future.
  warnings.warn(


In [69]:
trainer = base.DistilTrainer(
    args=training_args,
    train_dataset=all_train_data,
    eval_dataset=eval_data,
    compute_metrics=base.compute_metrics,
    model_init = lambda: get_BiLSTM(),
    #callbacks = [EarlyStoppingCallback(early_stopping_patience = 4)]
)
  

In [70]:
best_trial4 = trainer.hyperparameter_search(
    direction="maximize",
    backend="optuna",
    hp_space=hp_space,
    compute_objective=lambda metrics: metrics["eval_f1"],
    pruner=pruner,
    sampler=sampler,
    study_name="Test-Distill-aug",
    n_trials=150
)

[I 2025-03-16 09:29:44,460] A new study created in memory with name: Test-Distill-aug


Trial 0 with params: {'learning_rate': 0.0001025350969016849, 'weight_decay': 0.01, 'adam_beta1': 0.97, 'warmup_steps': 32, 'lambda_param': 0.1, 'temperature': 2.5}


[I 2025-03-16 09:31:15,774] Trial 0 pruned. 


Trial 1 with params: {'learning_rate': 1.4347159517201392e-05, 'weight_decay': 0.009000000000000001, 'adam_beta1': 0.96, 'warmup_steps': 38, 'lambda_param': 0.0, 'temperature': 7.0}


[I 2025-03-16 09:34:12,058] Trial 1 pruned. 


...

Trial 105 with params: {'learning_rate': 0.0035212827408528883, 'weight_decay': 0.008, 'adam_beta1': 0.93, 'warmup_steps': 0, 'lambda_param': 0.5, 'temperature': 4.5}


[I 2025-03-16 19:19:12,923] Trial 105 pruned. 


Trial 106 with params: {'learning_rate': 0.004533105118239366, 'weight_decay': 0.008, 'adam_beta1': 0.9400000000000001, 'warmup_steps': 0, 'lambda_param': 0.4, 'temperature': 6.0}


[W 2025-03-16 19:19:16,028] Trial 106 failed with parameters: {'learning_rate': 0.004533105118239366, 'weight_decay': 0.008, 'adam_beta1': 0.9400000000000001, 'warmup_steps': 0, 'lambda_param': 0.4, 'temperature': 6.0} because of the following error: KeyboardInterrupt().
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/optuna/study/_optimize.py", line 197, in _run_trial
    value_or_values = func(trial)
  File "/usr/local/lib/python3.10/dist-packages/transformers/integrations/integration_utils.py", line 250, in _objective
    trainer.train(resume_from_checkpoint=checkpoint, trial=trial)
  File "/usr/local/lib/python3.10/dist-packages/transformers/trainer.py", line 2241, in train
    return inner_training_loop(
  File "/usr/local/lib/python3.10/dist-packages/transformers/trainer.py", line 2581, in _inner_training_loop
    _grad_norm = self.accelerator.clip_grad_norm_(
  File "/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py", line 2509,

KeyboardInterrupt: 

In [71]:
print(best_trial4)

NameError: name 'best_trial4' is not defined

In [72]:
print("Best normal training score: ", best_trial)
print("Best distilation trianing score: ", best_trial2)
print("Best normal training score with augmentations: ", best_trial3)
print("Best distilation trianing score with augmentations: ",best_trial4)

Best normal training score:  BestRun(run_id='45', objective=0.7063463805279003, hyperparameters={'learning_rate': 0.004693546493886514, 'weight_decay': 0.002, 'adam_beta1': 0.9, 'warmup_steps': 1}, run_summary=None)
Best distilation trianing score:  BestRun(run_id='105', objective=0.48810144914827314, hyperparameters={'learning_rate': 0.004107822923895355, 'weight_decay': 0.003, 'adam_beta1': 0.93, 'warmup_steps': 0, 'lambda_param': 0.2, 'temperature': 2.5}, run_summary=None)
Best normal training score with augmentations:  BestRun(run_id='22', objective=0.777016449838325, hyperparameters={'learning_rate': 0.0026826241523527678, 'weight_decay': 0.009000000000000001, 'adam_beta1': 0.92, 'warmup_steps': 27}, run_summary=None)


NameError: name 'best_trial4' is not defined